In [1]:
import pandas as pd
import numpy as np
import os
import time
import random
import gensim
import numpy as np
import os
import torch
from gensim.models import KeyedVectors
from matplotlib import pyplot as plt
from matplotlib.pyplot import figure

/home/fatma/.local/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
def get_mean_vector(model, words):
    # remove out-of-vocabulary words
    # words: target list words
    # returns average vector for all words in target list
    import numpy as np
    words = [word for word in words if word in model.index_to_key]
    if len(words) >= 1:
        return np.mean(model[words], axis=0)
    else:
        return []

def mdi(mean, gini, weight):
    exp1 =  np.power(mean,weight) 
    exp2 = np.power((1 - gini),1-weight)
    return exp1 * exp2

def get_similarity_Scores(v1,v2):
    from numpy import dot
    from numpy.linalg import norm
    return dot(v1,v2)/(norm(v1)*norm(v2))

def normalize_data(a):
    normalizded_a = []
    amin, amax = min(a), max(a)
    for i in a:
        normalizded_a.append((i-amin) / (amax-amin))
    return normalizded_a
    
def get_similarity_scores_between_target_words_and_attribute_words(model, attribute_words, target_words):
    
    similarity_scores_summary = {}
    words = []
    mean_sim_socres = []

    target_words = [word for word in target_words if word in model.index_to_key]
    attribute_words = [word for word in attribute_words if word in model.index_to_key]
    
    if len(target_words) >= 1 and len(attribute_words) >=1:
        for i in target_words:
            similarity_scores = []
            words.append(i)
            for j in attribute_words:
                cos_sim = get_similarity_Scores(model[i], model[j])
                similarity_scores.append(cos_sim)
            mean_sim_socres.append(np.mean(normalize_data(similarity_scores)))

    similarity_scores_summary["word"] = words
    similarity_scores_summary["mean_sim_score"] = mean_sim_socres
    return similarity_scores_summary

def get_similarity_scores_between_avergare_target_vector_and_attribute_words(model, att_words, target_vector):
    # remove out-of-vocabulary words
    # att_words: wors in the attribute list
    # target_vector: average vector of all words in target group
    similarity_scores_summary = {}
    words_list = []
    similarity_scores = []
    words = [word for word in att_words if word in model.index_to_key]
    print(len(words))
    if len(words) >= 1:
        for i in words:
            print(i)
            words_list.append(i)
            cos_sim = get_similarity_Scores(model[i], target_vector)
            similarity_scores.append(cos_sim)
    similarity_scores_summary["words"] = words_list
    similarity_scores_summary["cos_sim_scores"] = similarity_scores
    similarity_scores_summary["sim_score"] = normalize_data(similarity_scores)

    return similarity_scores_summary


## Read profane words

In [2]:
data_folder = "../../Data/"
embeddings_folder = data_folder+"/word embeddings/"
results_folder = "Results/ethnicity_similarities/glove-wk/"

In [3]:
profane_words = open(data_folder+"swear_words.txt").read().splitlines()

## read word embeddings

In [4]:
def get_google_news_embeddings(filename,binary=False):
    w2v_model = gensim.models.KeyedVectors.load_word2vec_format(filename, binary=binary)
    return w2v_model


## word similarity

In [5]:
# convert text to w2v
#from gensim.scripts.glove2word2vec import glove2word2vec
#GLOVE_DIR = data_folder+"/glove.6B.300d_WP.txt"
#w2v_file = data_folder+"/wv_2_glove.6B.300d_WP.txt"
#glove2word2vec(GLOVE_DIR, w2v_file)

In [6]:
glove_wk_model = get_google_news_embeddings(embeddings_folder+"/Glove/glove.6B/glove_2_word2vec.6B.200d.txt")

## similar words

In [9]:
glove_wk_model.most_similar("girl")

[('boy', 0.8486549258232117),
 ('girls', 0.7696278691291809),
 ('woman', 0.7648226618766785),
 ('child', 0.7002282738685608),
 ('mother', 0.6969298124313354),
 ('teenage', 0.6899839043617249),
 ('boys', 0.6887997984886169),
 ('teen', 0.6872598528862),
 ('teenager', 0.6842572093009949),
 ('daughter', 0.6838235259056091)]

In [7]:
glove_wk_model.most_similar("queer")

[('transgender', 0.5460976362228394),
 ('lesbian', 0.5219112038612366),
 ('lgbt', 0.5063799619674683),
 ('lgbtq', 0.5030680894851685),
 ('bisexual', 0.5025513172149658),
 ('feminism', 0.4935998320579529),
 ('feminist', 0.4866087734699249),
 ('transgendered', 0.44645944237709045),
 ('sexualities', 0.4192824065685272),
 ('chicano', 0.4145326018333435)]

In [8]:
glove_wk_model.most_similar("queers")

[('gringos', 0.4799908697605133),
 ('freeloaders', 0.42081889510154724),
 ('hurray', 0.41508135199546814),
 ('foremothers', 0.4108246862888336),
 ('rap-rock', 0.4086662530899048),
 ('bubbas', 0.40684252977371216),
 ('laughers', 0.40594449639320374),
 ('sodomites', 0.40231892466545105),
 ('godless', 0.4009784460067749),
 ('mojos', 0.4002789855003357)]

In [12]:
glove_wk_model.most_similar("immigrant")

[('immigrants', 0.8401675224304199),
 ('migrant', 0.6586580276489258),
 ('immigration', 0.6520180702209473),
 ('undocumented', 0.6261692643165588),
 ('migrants', 0.6165194511413574),
 ('hispanic', 0.5675293803215027),
 ('worker', 0.5467345714569092),
 ('latino', 0.5261528491973877),
 ('parents', 0.5172895193099976),
 ('haitian', 0.5171931385993958)]

## minority and 
majority words

In [8]:
harmless_majority_words_clean = ["hetrosexual", "cisgender", "man","male","boy","son","father","husband","brother","white","caucasian",
                                 "european american","european", "norwegian", "canadian", "german", "australian", "english",
                                "french", "american", "swedish", "dutch"]

target_words = ["lesbian","gay","bisexual","transgender","tran","queer",
                "lgbt","lgbtq","homosexual", "woman", "female", "girl","wife","sister","daughter","mother", "non-binary",
               "african", "african american", "asian", "black", "hispanic", "latin", "mexican", "indian", "middle eastern",
                "arab"]

words = harmless_majority_words_clean + target_words

In [9]:
profane_vector = get_mean_vector(glove_wk_model, profane_words)
vec_majority_sim_dict = get_similarity_scores_between_avergare_target_vector_and_attribute_words(glove_wk_model, words, profane_vector)
pd.DataFrame(vec_majority_sim_dict).to_csv(results_folder+"_minority_and_majority_words_sim_to_profane_vector.csv")

44
cisgender
man
male
boy
son
father
husband
brother
white
caucasian
european
norwegian
canadian
german
australian
english
french
american
swedish
dutch
lesbian
gay
bisexual
transgender
tran
queer
lgbt
lgbtq
homosexual
woman
female
girl
wife
sister
daughter
mother
african
asian
black
hispanic
latin
mexican
indian
arab


In [10]:
figure(figsize=(25, 10), dpi=1200)
sorted_index = np.argsort(vec_majority_sim_dict["sim_score"])

x_axis = np.arange(len(vec_majority_sim_dict["words"]))
y_axis = [vec_majority_sim_dict["sim_score"][i] for i in sorted_index]
x_ticks = [vec_majority_sim_dict["words"][i] for i in sorted_index]
plt.bar(x_axis, y_axis)
plt.xticks(x_axis, x_ticks, fontsize=40, fontweight='bold', rotation=90)
plt.ylabel("similarity score", fontsize=40, fontweight='bold')
plt.yticks(np.arange(0.1,1.1,0.1),fontsize=40, fontweight='bold')
plt.savefig(results_folder+"similarity_score_of_minority_and_majority_words_to_profanity_vector.pdf", bbox_inches='tight')